In [ ]:
from mainnet_launch.database.schema.ensure_tables_are_current.using_onchain.not_order_dependent.about_incentives.update_destination_vault_balance_updated import *
from mainnet_launch.constants import *
from mainnet_launch.database.postgres_operations import get_full_table_as_df_with_tx_hash
from mainnet_launch.database.schema.full import IncentiveTokenBalanceUpdated, Tokens, DestinationStates
import plotly.express as px
import plotly.io as pio
pio.templates.default = "plotly_white"
df = get_full_table_as_df_with_tx_hash(IncentiveTokenBalanceUpdated)
destinations = get_full_table_as_df(Destinations)
tokens = get_full_table_as_df(Tokens)
destination_vault_address_to_symbol = dict(zip(destinations['destination_vault_address'], destinations['symbol']))
token_address_to_symbol = dict(zip(tokens['token_address'], tokens['symbol']))

states = get_full_table_as_df(DestinationStates)

states

df['destination_symbol'] = df['destination_vault_address'].map(destination_vault_address_to_symbol)
df['token_symbol'] = df['token_address'].map(token_address_to_symbol)
df['symbol'] = df['destination_symbol'] + ' - ' + df['token_symbol']
df = df.sort_index()
df['hours_between'] = (
    df.index.to_series()
      .groupby(df['symbol'])
      .diff()
      .dt.total_seconds()
      / 3600.0
)
df['datetime_claimed'] = df.index

In [ ]:
destinations

In [30]:
fig = px.scatter(
    df,
    x=df.index,
    y='hours_between',
    color='symbol',
    title='Destination Vault Balances Over Time',
)
fig.show()

## some new methods to try and catch this

True positive,
- We should have moved some rewards but did not. Urgent, need to fix
False positive 
- "Warning! we should have move some rewards but did not", 
- - False becuase we have moved rewards
- - Flase bacause there are no rewards to move


True Negative
- For X destination vault, we have claimed incentive tokens within the last 24 hours,
- - We have not claimed and we shoul dnot have claimed
- - we have claimed and we should have claimed|

- stipulations, missing a true positive is bad

In [ ]:
from datetime import datetime, timedelta, timezone

# Get the current time
now = datetime.now(timezone.utc)

# Calculate the threshold time (24 hours ago)
threshold_time = now - timedelta(hours=48)

# Group by symbol and find the max datetime_claimed
last_claimed = df.groupby('symbol')['datetime_claimed'].max()
symbols_over_24_hours = last_claimed[last_claimed < threshold_time].index.tolist()

symbols_claimed_voe

suspect_df = df[df['symbol'].isin(symbols_over_24_hours)]
px.scatter(
    suspect_df,
    x=suspect_df.index,
    y='hours_between',
    color='symbol',
    hover_data=['new_balance'],
    title='Destination Vault Balances Over Time (Suspect)',
)

# Filter symbols where the max datetime_claimed is more than 24 hours ago
print(len(symbols_over_24_hours), "symbols have not claimed incentives in the last 48 hours:")

108 symbols have not claimed incentives in the last 48 hours:


In [ ]:

# my code to catch destination vaults not getting liquidated properly; failed to catch this

fluid_destinations = ['0xE4545f9dBC30Ccb6Cda6930DDFd69f3D419FcB61', '0x28d2F508127B0617Ded8243836eB7b5787828648', '0x7876F91BB22148345b3De16af9448081E9853830']
sub_df = df[df['destination_vault_address'].isin(fluid_destinations)].copy()

sub_df = sub_df.sort_index()


px.scatter

array(['0x6f40d4A6237C257fff2dB00FA0510DeEECd303eb'], dtype=object)

In [44]:
px.scatter(
    sub_df,
    x=sub_df.index,
    y='hours_between',
    color='symbol',
    hover_data=['new_balance'],
    title='Destination Vault Balances Over Time (Suspect)',
).show()

In [ ]:
sub_df

In [ ]:
# there was a gap in claiming incentives between nov 20 and nov 27 for fluid USDC
#  incentive apr was > 1% () we had some money there, and there should have been expected incentives claimed but instead there were not

In [ ]:
# destination_vault_address	symbol	pool	underlying_name
# 1	0xE4545f9dBC30Ccb6Cda6930DDFd69f3D419FcB61	toke-USDC-fUSDT	0x5C20B550819128074FD538Edf79791733ccEdd18	Fluid Tether USD
# 2	0x28d2F508127B0617Ded8243836eB7b5787828648	toke-USDC-fsUSDS	0x2BBE31d63E6813E3AC858C04dae43FB2a72B0D11	Fluid Savings USDS
# 3	0x7876F91BB22148345b3De16af9448081E9853830	toke-USDC-fUSDC	0x9Fb7b4477576Fe5B32be4C1843aFB1e55F251B33	Fluid USD Coin

